In [27]:
import requests
import json
import pandas as pd

def generate_token(portal_url: str, username: str, password: str, referer: str = None) -> str:
    """
    Generate an ArcGIS token using username and password.
    """
    token_params = {
        "username": username,
        "password": password,
        "client": "referer" if referer else "requestip",
        "referer": referer or "",
        "f": "json"
    }

    response = requests.post(portal_url, data=token_params)
    data = response.json()

    if "token" not in data:
        raise Exception(f"Failed to get token: {data}")
    return data["token"]


def query_arcgis_layer(service_url: str, token: str, where: str = "1=1", out_fields: str = "*", return_geometry: bool = False) -> dict:
    """
    Query an ArcGIS MapServer/FeatureServer layer.
    """
    params = {
        "where": where,
        "outFields": out_fields,
        "returnGeometry": str(return_geometry).lower(),
        "f": "json",
        "token": token
    }

    response = requests.get(service_url, params=params)
    if response.status_code != 200:
        raise Exception(f"Error {response.status_code}: {response.text}")

    return response.json()


def arcgis_to_dataframe(data: dict) -> pd.DataFrame:
    """Convert ArcGIS REST JSON to pandas DataFrame."""
    if "features" not in data or len(data["features"]) == 0:
        print("⚠️ No features found.")
        return pd.DataFrame()
    
    # Flatten attributes (and geometry if present)
    df = pd.json_normalize(data["features"])
    
    # Usually attributes are under "attributes.*"
    # Let's remove that prefix for readability
    df.columns = [col.replace("attributes.", "") for col in df.columns]
    return df


def main():
    # --- Config ---
    portal_url = "https://geoportal.mnmsugarhub.com/portal/sharing/rest/generateToken"
    username = "adm.gis"
    password = "GIS@portal1234!"
    referer = "https://geoportal.mnmsugarhub.com"
    mapserver_url = "https://geoportal.mnmsugarhub.com/server/rest/services/Paddock_Naming_Concept_GPA/MapServer/"
    level = [
        {"name":"Mill", "layerId":2, "level":1},
        {"name":"Region", "layerId":1, "level":2},
        {"name":"Farm", "layerId":3, "level":3},
        {"name":"Block", "layerId":5, "level":4},
        {"name":"Paddock", "layerId":4, "level":5},
    ]


    # --- Step 1: Get Token ---
    print("🔐 Generating token...")
    token = generate_token(portal_url, username, password, referer)
    print("✅ Token generated successfully")

    # --- Step 2: Query MapServer ---
    print("📡 Querying ArcGIS service...")

    level_unit = pd.DataFrame()

    for l in level:
        query_url = f"{mapserver_url}/{l['layerId']}/query"

        data = query_arcgis_layer(query_url, token)
        df = arcgis_to_dataframe(data)
        df['level'] = l["name"]
        df['level_id'] = l["level"]

        level_unit = pd.concat([level_unit, df], ignore_index=True)

    # return level_unit
    cols = ["level", "level_id"] + [c for c in level_unit.columns if c not in ["level", "level_id"]]
    level_unit = level_unit[cols]
    
    all_structure = []
    
    for i, row in level_unit.iterrows():
        if row['level_id'] == 1:
            level_1 = row[["level","level_id","fid_1", "mill_id","mill","st_area(shape)"]].to_dict()
            child1 = []

            for j, row2 in level_unit.iterrows():
                if row2['level_id'] == 2:
                    level_2 = row2[["level","level_id","fid_1", "mill_id","region_id","mill","region","st_area(shape)"]].to_dict()
                    child1.append(level_2)
                    child2 = []

                    for k, row3 in level_unit.iterrows():
                        if row3['level_id'] == 3:
                            level_3 = row3[["level","level_id","fid_1", "mill_id","region_id","farm_id","mill","region", "farm","farm","st_area(shape)"]].to_dict()
                            child2.append(level_3)
                            child3 = []
                            
                            for l, row4 in level_unit.iterrows():
                                if row4['level_id'] == 4:
                                    level_4 = row4[["level","level_id","fid_1", "mill_id","region_id","farm_id","block_id", "mill","region", "farm","block","st_area(shape)"]].to_dict()
                                    child3.append(level_4)
                                    child4 = []

                                    for m, row5 in level_unit.iterrows():
                                        if row5['level_id'] == 5:
                                            level_5 = row5[["level","level_id","fid_1", "mill_id","region_id","farm_id","block_id","paddock_id", "mill","region", "farm","block","paddock","st_area(shape)"]].to_dict()
                                            child4.append(level_5)


                                    level_4['child'] = child4
                            level_3['child'] = child3
                    level_2['child'] = child2
            level_1['child'] = child1

            all_structure.append(level_1)
    
    print(all_structure)
    json_output = json.dumps(all_structure, indent=2)

    # Print preview
    print("✅ Hierarchical JSON structure created successfully!")
    print(json_output[:1000], "...")  # print first part to avoid overload

    # --- Step 6: Save to file ---
    with open("paddock_structure.json", "w", encoding="utf-8") as f:
        f.write(json_output)



if __name__ == "__main__":
    main()


🔐 Generating token...
✅ Token generated successfully
📡 Querying ArcGIS service...
[{'level': 'Mill', 'level_id': 1, 'fid_1': '1', 'mill_id': '1', 'mill': 'Jagebob Mill', 'st_area(shape)': 343977019.9518076, 'child': [{'level': 'Region', 'level_id': 2, 'fid_1': 'JAGF', 'mill_id': '1', 'region_id': '1', 'mill': 'Jagebob Mill', 'region': 'JAGF', 'st_area(shape)': 343977019.9518076, 'child': [{'level': 'Farm', 'level_id': 3, 'fid_1': '1', 'mill_id': '1', 'region_id': '1', 'farm_id': '1', 'mill': 'Jagebob Mill', 'region': 'JAGF', 'farm': '1', 'st_area(shape)': 49549240.59192945, 'child': [{'level': 'Block', 'level_id': 4, 'fid_1': '1-A', 'mill_id': '1', 'region_id': '1', 'farm_id': '1', 'block_id': 'A', 'mill': 'Jagebob Mill', 'region': 'JAGF', 'farm': '1', 'block': 'A', 'st_area(shape)': 5844849.402105655, 'child': [{'level': 'Paddock', 'level_id': 5, 'fid_1': '1-A-1', 'mill_id': '1', 'region_id': '1', 'farm_id': '1', 'block_id': 'A', 'paddock_id': '1', 'mill': 'Jagebob Mill', 'region': 'J